# Collect data comment Youtube Rewind Indonesia 2016 dengan Google Client API

Import library

In [1]:
from dotenv import load_dotenv
import os
import googleapiclient.discovery
import pandas as pd
from pymongo import MongoClient

Mengakses value dari file env

In [2]:
# Memuat value dari file .env
load_dotenv()

dev = os.getenv('API_KEY_1')
mongodb_url = os.getenv('URL_SANDY')
local_url = os.getenv('URL_LOCAL')

Inisialisasi videoID dan database name

In [3]:
video_id = "1ZIGLm5cuDo"
database_name = "youtube_rewind_indonesia"
collection_name = "collect_2016"

Proses collect data

In [4]:
# Konfigurasi nama layanan API dan versi yang akan digunakan
api_service_name = "youtube"
api_version = "v3"

DEVELOPER_KEY = dev

# Koneksi ke MongoDB
client = MongoClient(local_url)
db = client[database_name]
collection = db[collection_name]

# Membangun objek YouTube API dengan menggunakan kunci pengembang dan versi API yang ditentukan
youtube = googleapiclient.discovery.build(
    api_service_name, api_version, developerKey=DEVELOPER_KEY)

# Membuat permintaan (request) untuk mendapatkan data komentar dari video tertentu
request = youtube.commentThreads().list(
    part="snippet",
    videoId=video_id,  # ID video yang akan diambil komentarnya
    maxResults=100  # Jumlah maksimum komentar yang akan diambil
)

# Inisialisasi list kosong untuk menyimpan komentar
comments = []

# Mengirimkan permintaan dan mendapatkan respons
response = request.execute()

counter = 1

# Mendapatkan komentar dari respons
for item in response['items']:
    comment = item['snippet']['topLevelComment']['snippet']
    public = item['snippet']['isPublic']
    # Menambahkan semua atribut komentar ke dalam list comments dalam bentuk dictionary
    comments.append({
        'authorDisplayName': comment['authorDisplayName'], # Nama penulis komentar
        'authorProfileImageUrl': comment['authorProfileImageUrl'], # URL gambar profil penulis
        'authorChannelUrl': comment['authorChannelUrl'], # URL channel penulis
        'channelId': comment['channelId'], # ID channel penulis
        'publishedAt': comment['publishedAt'], # Waktu publikasi komentar
        'updatedAt': comment['updatedAt'], # Waktu update komentar
        'likeCount': comment['likeCount'], # Jumlah suka komentar
        'textDisplay': comment['textDisplay'], # Isi komentar yang diformat dengan tautan dan emoji yang diproses
        'textOriginal': comment['textOriginal'], # Isi komentar
        'viewerRating': comment['viewerRating'], # Rating yang diberikan oleh pengguna
        'isPublic': public # Status publikasi komentar
    })

    # Menyisipkan data ke MongoDB
    collection.insert_one(comment)
    print(f"{counter} : {comment['textOriginal']}")
    counter+=1

# Melakukan iterasi untuk mengambil komentar dari halaman berikutnya jika ada
while (1 == 1):
    try:
        nextPageToken = response['nextPageToken']  # Mengambil token untuk halaman berikutnya
    except KeyError:
        break  # Keluar dari loop jika tidak ada halaman berikutnya
    
    nextPageToken = response['nextPageToken']  # Mengambil token untuk halaman berikutnya
    
    # Membuat permintaan baru dengan menggunakan token halaman berikutnya
    nextRequest = youtube.commentThreads().list(
        part="snippet", 
        videoId=video_id,  # ID video (opsional jika tetap sama dengan sebelumnya)
        maxResults=100,  # Jumlah maksimum komentar per halaman
        pageToken=nextPageToken  # Token untuk halaman berikutnya
    )
    # Mengirimkan permintaan baru dan mendapatkan respons
    response = nextRequest.execute()

    # Mendapatkan komentar dari respons dan menambahkannya ke dalam list comments
    for item in response['items']:
        comment = item['snippet']['topLevelComment']['snippet']
        public = item['snippet']['isPublic']
        # Menambahkan semua atribut komentar ke dalam list comments dalam bentuk dictionary
        comments.append({
            'authorDisplayName': comment['authorDisplayName'], # Nama penulis komentar
            'authorProfileImageUrl': comment['authorProfileImageUrl'], # URL gambar profil penulis
            'authorChannelUrl': comment['authorChannelUrl'], # URL channel penulis
            'channelId': comment['channelId'], # ID channel penulis
            'publishedAt': comment['publishedAt'], # Waktu publikasi komentar
            'updatedAt': comment['updatedAt'], # Waktu update komentar
            'likeCount': comment['likeCount'], # Jumlah suka komentar
            'textDisplay': comment['textDisplay'], # Isi komentar yang diformat dengan tautan dan emoji yang diproses
            'textOriginal': comment['textOriginal'], # Isi komentar
            'viewerRating': comment['viewerRating'], # Rating yang diberikan oleh pengguna
            'isPublic': public # Status publikasi komentar
        })
        
        # Menyisipkan data ke MongoDB
        collection.insert_one(comment)
        print(f"{counter} : {comment['textOriginal']}")
        counter+=1

1 : Rewind paling bnyk memori soalnya di jaman itu setiap Youtuber saling collab, udh gitu deket banget dengan viewers.

Benar-benar kek satu komunitas.
2 : 3:30 BeaconCream🗿🗿
3 : Seru banget liat ulang" dari yang 2023
4 : Haii aku dari 2024🥹🇮🇩
5 : Halo dari 2024
6 : kangen bat anjay
7 : ada beaconcreamcuy
8 : KANGEN BANGET JAMAN JAMAN INII❤❤
9 : halo aku dari masa depan
10 : gabisa dipungkirin ini youtube rewind terbaik anjir
11 : Sumpah nonton rewind ini di tahun 2024 tuh jadi kangen ke masa dulu lagi, dimana youtube masih di penuhi sama konten yang berisi dan pastinya seru.. Tapi rewind 2023 gak kalah kerennya sih
12 : bgsd kesini gara gara abis nonton PWK kwkw
13 : GILAAKK OLD BUT GOLD
14 : dan aku kembali menontonnya di 2024 :')
15 : Anjir arap vibesnya masih asik banget jaman segitu😂
16 : huuuuuaaaa kangen yang ini 😂🤣😅😅😅
17 : Still one of the best
18 : Dari 2024🙂
19 : Rekam jejak 2024. kita gabisa kembali ke masa lalu namun cuman rekam jejak yang bisa jadi kenangan untuk semua. s

In [5]:
# Membuat DataFrame dari list comments dengan kolom-kolom yang ditentukan
df = pd.DataFrame(comments)
# Menampilkan informasi DataFrame seperti jumlah baris dan tipe data kolom
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 70135 entries, 0 to 70134
Data columns (total 11 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   authorDisplayName      70135 non-null  object
 1   authorProfileImageUrl  70135 non-null  object
 2   authorChannelUrl       70135 non-null  object
 3   channelId              70135 non-null  object
 4   publishedAt            70135 non-null  object
 5   updatedAt              70135 non-null  object
 6   likeCount              70135 non-null  int64 
 7   textDisplay            70135 non-null  object
 8   textOriginal           70135 non-null  object
 9   viewerRating           70135 non-null  object
 10  isPublic               70135 non-null  bool  
dtypes: bool(1), int64(1), object(9)
memory usage: 5.4+ MB


In [6]:
df

authorDisplayName  \
0                          @Fiammawan1   
1                       @PemainRoblox2   
2                             @Zan-too   
3             @adindatiaraagustine6028   
4                    @rnggaakhaira6602   
...                                ...   
70130  @lalumuhammadnaveenbomantar1066   
70131         @keisyanoviansyahnur2857   
70132                  @donylukito1058   
70133                         @fjr1746   
70134              @yustrisiadinda7687   

                                   authorProfileImageUrl  \
0      https://yt3.ggpht.com/_e9Fqq5cqPF2-9fSB3Uuu3-H...   
1      https://yt3.ggpht.com/ruCvUZnnBNROJMZFxR7eUxND...   
2      https://yt3.ggpht.com/ytc/AIdro_lqybv1ymmQZzV-...   
3      https://yt3.ggpht.com/ytc/AIdro_nZTGo3ibibGPIc...   
4      https://yt3.ggpht.com/ytc/AIdro_miy4I4tWQShzVX...   
...                                                  ...   
70130  https://yt3.ggpht.com/ytc/AIdro_lThIcUkdURy36C...   
70131  https://yt3.ggpht.com/ytc/AIdro_mNGnEcqEDgIssF...   
70132  https://yt3.ggpht.com/ytc/AIdro_kZXf00HgnNSZBH...   
70133  https://yt3.ggpht.com/ytc/AIdro_mlJRhIYHmv0vHd...   
70134  https://yt3.ggpht.com/ytc/AIdro_n04FDP-09gmUlz...   

                                        authorChannelUrl  \
0                     http://www.youtube.com/@Fiammawan1   
1                  http://www.youtube.com/@PemainRoblox2   
2                        http://www.youtube.com/@Zan-too   
3        http://www.youtube.com/@adindatiaraagustine6028   
4               http://www.youtube.com/@rnggaakhaira6602   
...                                                  ...   
70130  http://www.youtube.com/@lalumuhammadnaveenboma...   
70131    http://www.youtube.com/@keisyanoviansyahnur2857   
70132             http://www.youtube.com/@donylukito1058   
70133                    http://www.youtube.com/@fjr1746   
70134         http://www.youtube.com/@yustrisiadinda7687   

                      channelId           publishedAt             updatedAt  \
0      UC-z1ubmS-iHMVr83EEwRS2g  2024-05-24T18:10:30Z  2024-05-24T18:10:30Z   
1      UC-z1ubmS-iHMVr83EEwRS2g  2024-05-24T14:22:36Z  2024-05-24T14:22:36Z   
2      UC-z1ubmS-iHMVr83EEwRS2g  2024-05-24T07:37:13Z  2024-05-24T07:37:13Z   
3      UC-z1ubmS-iHMVr83EEwRS2g  2024-05-24T07:33:35Z  2024-05-24T07:33:35Z   
4      UC-z1ubmS-iHMVr83EEwRS2g  2024-05-23T18:25:48Z  2024-05-23T18:25:53Z   
...                         ...                   ...                   ...   
70130  UC-z1ubmS-iHMVr83EEwRS2g  2016-12-18T12:16:16Z  2016-12-18T12:16:16Z   
70131  UC-z1ubmS-iHMVr83EEwRS2g  2016-12-18T12:16:16Z  2016-12-18T12:16:16Z   
70132  UC-z1ubmS-iHMVr83EEwRS2g  2016-12-18T12:16:16Z  2016-12-18T12:16:16Z   
70133  UC-z1ubmS-iHMVr83EEwRS2g  2016-12-18T12:16:15Z  2016-12-18T12:16:15Z   
70134  UC-z1ubmS-iHMVr83EEwRS2g  2016-12-18T12:16:14Z  2016-12-18T12:16:14Z   

       likeCount                                        textDisplay  \
0              2  Rewind paling bnyk memori soalnya di jaman itu...   
1              0  <a href="https://www.youtube.com/watch?v=1ZIGL...   
2              1        Seru banget liat ulang&quot; dari yang 2023   
3              0                              Haii aku dari 2024🥹🇮🇩   
4              1                                     Halo dari 2024   
...          ...                                                ...   
70130          0                                           pertamax   
70131          0                                               Firs   
70132          0                                            pertama   
70133          0                                            KEREEEN   
70134          1                                              first   

                                            textOriginal viewerRating  \
0      Rewind paling bnyk memori soalnya di jaman itu...         none   
1                                     3:30 BeaconCream🗿🗿         none   
2                 Seru banget liat ulang" dari yang 2

In [7]:
df.sort_values(by='likeCount', ascending=False)[0:10]

authorDisplayName                              authorProfileImageUrl  \
66681          @Tim2one  https://yt3.ggpht.com/ytc/AIdro_koWWb9JTasq6o_...   
10166      @TheJooomers  https://yt3.ggpht.com/ytc/AIdro_nWvub452cuDU6x...   
24218  @famousytber3336  https://yt3.ggpht.com/ytc/AIdro_mbP9YGUY0rbpn6...   
7462     @fxntastic7111  https://yt3.ggpht.com/OvRvCUwt3tNqGqy-Fp6zCX0m...   
13407      @TheJooomers  https://yt3.ggpht.com/ytc/AIdro_nWvub452cuDU6x...   
22771        @SanzLemon  https://yt3.ggpht.com/ytc/AIdro_n7u2LrICyFL4_L...   
24424            @dipqi  https://yt3.ggpht.com/FaxCVsTbpf63F3Wj1uTLKx3_...   
67194  @SaaihHalilintar  https://yt3.ggpht.com/ytc/AIdro_mSMCHv47VuesS5...   
26858      @GvmzyGaming  https://yt3.ggpht.com/ytc/AIdro_lSpoi9D5GhtuiP...   
22554       @Kenandgrat  https://yt3.ggpht.com/n89petb7QEqkLHzuH-4O6R2N...   

                              authorChannelUrl                 channelId  \
66681          http://www.youtube.com/@Tim2one  UC-z1ubmS-iHMVr83EEwRS2g   
10166      http://www.youtube.com/@TheJooomers  UC-z1ubmS-iHMVr83EEwRS2g   
24218  http://www.youtube.com/@famousytber3336  UC-z1ubmS-iHMVr83EEwRS2g   
7462     http://www.youtube.com/@fxntastic7111  UC-z1ubmS-iHMVr83EEwRS2g   
13407      http://www.youtube.com/@TheJooomers  UC-z1ubmS-iHMVr83EEwRS2g   
22771        http://www.youtube.com/@SanzLemon  UC-z1ubmS-iHMVr83EEwRS2g   
24424            http://www.youtube.com/@dipqi  UC-z1ubmS-iHMVr83EEwRS2g   
67194  http://www.youtube.com/@SaaihHalilintar  UC-z1ubmS-iHMVr83EEwRS2g   
26858      http://www.youtube.com/@GvmzyGaming  UC-z1ubmS-iHMVr83EEwRS2g   
22554       http://www.youtube.com/@Kenandgrat  UC-z1ubmS-iHMVr83EEwRS2g   

                publishedAt             updatedAt  likeCount  \
66681  2016-12-18T12:34:19Z  2016-12-18T12:34:19Z      16024   
10166  2020-07-06T13:29:11Z  2020-07-06T13:29:11Z      15031   
24218  2018-12-08T08:44:25Z  2018-12-08T08:44:25Z      12317   
7462   2020-11-28T14:02:14Z  2020-11-28T14:02:14Z       7852   
13407  2019-10-14T05:37:10Z  2019-10-14T05:37:10Z       7365   
22771  2018-12-14T15:48:37Z  2018-12-14T15:48:37Z       6546   
24424  2018-12-07T02:31:54Z  2018-12-07T02:31:54Z       6087   
67194  2016-12-18T12:30:40Z  2016-12-18T12:30:40Z       5594   
26858  2018-09-13T13:30:48Z  2018-09-13T13:30:48Z       5592   
22554  2018-12-14T16:11:22Z  2018-12-14T16:11:22Z       5020   

                                             textDisplay  \
66681      Proud to direct this baby. SALUTE TO YOU ALL!   
10166  2020 Harus begini lagi yah :) yang 2016 ... Go...   
24218  Yang Kecewa Sama YouTube Rewind Global 2018 Ka...   
7462   Let&#39;s be honest, kita semua merindukan you...   
13407                       Still best :) - October 2019   
22771  Yang udah nonton YT Rewind 2018 dr Live Tahuka...   
24424                         masih best sampe sekarang.   
67194  Memang Chandraliow dan Rezaoktovian yang palin...   
26858  Siapa yang nonton September 2018??<br>Apakah k...   
22554                                     Kangen :&#39;(   

                                            textOriginal viewerRating  \
66681      Proud to direct this baby. SALUTE TO YOU ALL!         none   
10166  2020 Harus begini lagi yah :) yang 2016 ... Go...         none   
24218  Yang Kecewa Sama YouTube Rewind Global 2018 Ka...         none   
7462   Let's be honest, kita semua merindukan youtube...         none   
13407                       Still best :) - October 2019         none   
22771  Yang udah nonton YT Rewind 2018 dr Live Tahuka...         none   
24424                         masih best sampe sekarang.         none   
67194  Memang Chandraliow dan Rezaoktovian yang palin...         none   
26858  Siapa yang nonton September 2018??\nApakah kal...         none   
22554                                         Kangen :'(         none   

       isPublic  
66681      True  
10166      True  
24218      True  
7462       True  
13407      True  
22771      True  
24424      Tru

Migrasi dari MongoDB Local ke MongoDB Atlas

In [8]:
# Koneksi ke MongoDB lokal
local_client = MongoClient(local_url)
local_db = local_client[database_name]
local_collection = local_db[collection_name]

# Koneksi ke MongoDB Atlas
atlas_client = MongoClient(mongodb_url)
atlas_db = atlas_client[database_name]
atlas_collection = atlas_db[collection_name]

# Ambil semua dokumen dari koleksi MongoDB lokal
documents = list(local_collection.find())

# Masukkan dokumen ke MongoDB Atlas
if documents:
    atlas_collection.insert_many(documents)
    print(f'{len(documents)} dokumen berhasil dipindahkan dari MongoDB lokal ke MongoDB Atlas.')
else:
    print('Tidak ada dokumen yang ditemukan di MongoDB lokal.')

# Tutup koneksi
local_client.close()
atlas_client.close()

ServerSelectionTimeoutError: SSL handshake failed: ac-bzbv7pi-shard-00-00.tux1wrd.mongodb.net:27017: [SSL: TLSV1_ALERT_INTERNAL_ERROR] tlsv1 alert internal error (_ssl.c:1006) (configured timeouts: socketTimeoutMS: 20000.0ms, connectTimeoutMS: 20000.0ms),SSL handshake failed: ac-bzbv7pi-shard-00-01.tux1wrd.mongodb.net:27017: [SSL: TLSV1_ALERT_INTERNAL_ERROR] tlsv1 alert internal error (_ssl.c:1006) (configured timeouts: socketTimeoutMS: 20000.0ms, connectTimeoutMS: 20000.0ms),SSL handshake failed: ac-bzbv7pi-shard-00-02.tux1wrd.mongodb.net:27017: [SSL: TLSV1_ALERT_INTERNAL_ERROR] tlsv1 alert internal error (_ssl.c:1006) (configured timeouts: socketTimeoutMS: 20000.0ms, connectTimeoutMS: 20000.0ms), Timeout: 30s, Topology Description: <TopologyDescription id: 66515f9ad882d1f847e05667, topology_type: ReplicaSetNoPrimary, servers: [<ServerDescription ('ac-bzbv7pi-shard-00-00.tux1wrd.mongodb.net', 27017) server_type: Unknown, rtt: None, error=AutoReconnect('SSL handshake failed: ac-bzbv7pi